# CSE6242 - HW3 - Q1

Pyspark Imports

In [1]:
### DO NOT MODIFY THIS CELL ###
import pyspark
from pyspark.sql import SQLContext
from pyspark.sql.functions import hour, when, col, date_format, to_timestamp, round, coalesce
from pyspark.sql.functions import *

Initialize PySpark Context

In [2]:
### DO NOT MODIFY THIS CELL ###
sc = pyspark.SparkContext(appName="HW3-Q1")
sqlContext = SQLContext(sc)

Setting default log level to "WARN".
To adjust logging level use sc.setLogLevel(newLevel). For SparkR, use setLogLevel(newLevel).
23/10/18 14:58:22 WARN NativeCodeLoader: Unable to load native-hadoop library for your platform... using builtin-java classes where applicable
23/10/18 14:58:22 WARN Utils: Service 'SparkUI' could not bind on port 4040. Attempting port 4041.
23/10/18 14:58:22 WARN Utils: Service 'SparkUI' could not bind on port 4041. Attempting port 4042.
23/10/18 14:58:22 WARN Utils: Service 'SparkUI' could not bind on port 4042. Attempting port 4043.
/usr/local/lib/python3.9/dist-packages/pyspark/sql/context.py:113: FutureWarning: Deprecated in 3.0.0. Use SparkSession.builder.getOrCreate() instead.
  warnings.warn(


Define function for loading data

In [3]:
### DO NOT MODIFY THIS CELL ###
def load_data():
    df = sqlContext.read.option("header",True) \
     .csv("yellow_tripdata_2019-01_short.csv")
    return df

### Q1.a

Perform data casting to clean incoming dataset

In [4]:
def clean_data(df):
    '''
    input: df a dataframe
    output: df a dataframe with the all the original columns
    '''
    
    # START YOUR CODE HERE ---------
    from pyspark.sql.types import StructField, StructType, IntegerType, TimestampType, FloatType, StringType

    df = df.withColumn("passenger_count", df["passenger_count"].cast(IntegerType()))
    df = df.withColumn("total_amount", df["total_amount"].cast(FloatType()))
    df = df.withColumn("tip_amount", df["tip_amount"].cast(FloatType()))
    df = df.withColumn("trip_distance", df["trip_distance"].cast(FloatType()))
    df = df.withColumn("fare_amount", df["fare_amount"].cast(FloatType()))
    df = df.withColumn("tpep_pickup_datetime", df["tpep_pickup_datetime"].cast(TimestampType()))
    df = df.withColumn("tpep_dropoff_datetime", df["tpep_dropoff_datetime"].cast(TimestampType()))

    # END YOUR CODE HERE -----------
    
    return df

### Q1.b

Find rate per person for based on how many passengers travel between pickup and dropoff locations. 

In [5]:
def common_pair(df):
    '''
    input: df a dataframe
    output: df a dataframe with following columns:
            - PULocationID
            - DOLocationID
            - passenger_count
            - per_person_rate
            
    per_person_rate is the total_amount per person for a given pair.
    
    '''
    
    # START YOUR CODE HERE ---------
    from pyspark.sql import Window

    partition_cols = ['PULocationID','DOLocationID']

    group_by_result = df.groupBy(partition_cols).count()
    # group_by_result.show()

    # Filter out any trips that have the same pick-up and drop-off location. 
    df_temp = df.filter((df.PULocationID != df.DOLocationID))
    # group_by_result_difference_location.show()

    # # [4 pts] You will be modifying the function common_pair. 
    # # Return the top 10 pickup-dropoff location pairs that have the highest number of total passengers who have traveled between them. 
    # # Sort the location pairs by total passengers. 
    df_temp = df_temp.withColumn("passenger_count", sum("passenger_count").over(Window.partitionBy(*partition_cols)))
    
    # # For each location pair, also compute 
    #     # the average amount per passenger over all trips (name this per_person_rate), utilizing total_amount.
    df_temp = df_temp.withColumn("total_amount_partition", sum("total_amount").over(Window.partitionBy(*partition_cols)))
    df_temp = df_temp.withColumn("per_person_rate",col("total_amount_partition")/col("passenger_count"))
    
    # # For pairs with the same total passengers, 
    #     # sort them in descending order of per_person_rate.
    # # Rename the column for total passengers to passenger_count. 
    df_temp = df_temp.select(['PULocationID','DOLocationID','passenger_count','per_person_rate']).distinct()
    df_joined  = group_by_result.join(df_temp, partition_cols)
    df_joined = df_joined.orderBy(['passenger_count','per_person_rate'], ascending=False).limit(10)
    df_output = df_joined.drop('count')
    # END YOUR CODE HERE -----------
    
    return df_output

### Q1.c

Find trips which trip distances generate the highest tip percentage.

In [6]:
def distance_with_most_tip(df):
    '''
    input: df a dataframe
    output: df a dataframe with following columns:
            - trip_distance
            - tip_percent
            
    trip_percent is the percent of tip out of fare_amount
    
    '''
    
    # START YOUR CODE HERE ---------
    
    # END YOUR CODE HERE -----------
    
    return df

### Q1.d

Determine the average speed at different times of day.

In [7]:
def time_with_most_traffic(df):
    '''
    input: df a dataframe
    output: df a dataframe with following columns:
            - time_of_day
            - am_avg_speed
            - pm_avg_speed
            
    trip_percent is the percent of tip out of fare_amount
    
    '''
    
    # START YOUR CODE HERE ---------

    # END YOUR CODE HERE -----------
    
    return df

### The below cells are for you to investigate your solutions and will not be graded
## Ensure they are commented out prior to submitting to Gradescope to avoid errors

In [8]:
# df = load_data()
# df = clean_data(df)
# common_pair(df).show()
# distance_with_most_tip(df).show()
# time_with_most_traffic(df).show()

+------------+------------+---------------+------------------+
|PULocationID|DOLocationID|passenger_count|   per_person_rate|
+------------+------------+---------------+------------------+
|         239|         238|             62|  4.26274198870505|
|         237|         236|             60| 4.482500068346659|
|         263|         141|             52|3.4190384974846473|
|         161|         236|             42| 5.368571440378825|
|         148|          79|             42| 4.711904752822149|
|         142|         238|             39|  5.05487182812813|
|         141|         236|             37| 4.355675723101641|
|         239|         143|             37| 4.252162224537617|
|         239|         142|             35| 3.817714350564139|
|          79|         170|             34| 6.394705884596881|
+------------+------------+---------------+------------------+

